# Voronoi to Mascon
Here we take the output of `spherical_voronoi.ipynb` and convert the Voronoi regions into their harmonic representations as mascons and evaluate the corresponding sensitivity kernels.

In [1]:
#-- load required modules
import os
import sys
import copy
import pickle
import numpy as np
import pandas as pd
import geopandas as gpd
import plotly
import plotly.graph_objs as go
import matplotlib.pyplot as plt
from mpl_toolkits import mplot3d
from descartes import PolygonPatch
from shapely.geometry import Polygon,Point
from matplotlib.collections import PatchCollection
from scipy.spatial import SphericalVoronoi,geometric_slerp

In [2]:
#-- also import pyglates for calculating centroids on spherical surface
sys.path.append(os.path.expanduser('~/pygplates_rev28_python37_MacOS64'))
import pygplates

We also need [`gravity_toolkits`](https://github.com/yaramohajerani/read-GRACE-harmonics) modules created by Tyler Sutterley in order to perform the harmonics conversion and kernel tests.

In [3]:
sys.path.append(os.path.expanduser('~/read-GRACE-harmonics'))
sys.path.append(os.path.expanduser('~/read-GRACE-geocenter'))
from gravity_toolkit.gen_stokes import gen_stokes
from gravity_toolkit.ncdf_stokes import ncdf_stokes
from gravity_toolkit.ncdf_write import ncdf_write
from gravity_toolkit.read_love_numbers import read_love_numbers
from gravity_toolkit.plm_mohlenkamp import plm_mohlenkamp

In [4]:
#-- First load the saved SphericalVoronoi object
with open(os.path.join(os.getcwd(),'data','sv_obj'), 'rb') as in_file:
    sv = pickle.load(in_file)

In [5]:
#-- plot the configuration
plotly.offline.init_notebook_mode()

#-- plot generators
gens = go.Scatter3d(x=sv.points[:, 0],y=sv.points[:, 1],z=sv.points[:, 2],mode='markers',marker={'size': 3,'opacity': 0.8,'color': 'blue'},name='Generator Points')

data = [gens]

for region in sv.regions:
    n = len(region)
    t = np.linspace(0,1,50)
    for i in range(n):
        start = sv.vertices[region][i]
        end = sv.vertices[region][(i + 1) % n]
        result = np.array(geometric_slerp(start, end, t))
        edge = go.Scatter3d(x=result[..., 0],y=result[..., 1],z=result[..., 2],mode='lines',line={'width': 1,'color': 'black'},name='region edge',showlegend=False)
        data.append(edge)

#-- configure layout
layout = go.Layout(margin={'l': 0, 'r': 0, 'b': 0, 't': 0},title={
        'text': "Spherical Voronoi Regions",
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'})

plot_figure = go.Figure(data=data, layout=layout)

#-- render plot
plotly.offline.iplot(plot_figure)

In [6]:
#-- Now we make a high-res grid so we can rasterize the polygons onto a grid
DDEG = 0.25
lons = np.arange(-180,180+DDEG,DDEG)
lats = np.arange(-90,90+DDEG,DDEG)
glat,glon = np.meshgrid(lats,lons)
#-- flatten the grid for easier processing
glon = glon.flatten()
glat = glat.flatten()

In [7]:
#-- set harmonic parameters
LMAX = 60
LMIN = 0

In [8]:
#-- read love numbers required for generating geoid harmonics
hl,kl,ll = read_love_numbers(os.path.expanduser('~/read-GRACE-harmonics/gravity_toolkit/data/love_numbers'),REFERENCE='CF')

In [9]:
#-- create Legendre polynomials
th = (90.0 - lats)*np.pi/180.0
plm = plm_mohlenkamp(LMAX, np.cos(th))

Loop through each voronoi region and check if points are within polygon. If an element falls inside the polygon (mascon), we change it's value to 1 cmWE. Otherwise it will be 0 cmWE.

In [10]:
Ylms = {}
for i,region in enumerate(sv.regions):
    #-- intitialize mascon data as all zeros (no mass)
    mass = np.zeros(len(glon))
    #-- get vertices of region
    reg_vert = sv.vertices[region]
    #-- create polygon from vertices on surface of sphere
    poly = pygplates.PolygonOnSphere(reg_vert)
    #-- loop through grid points to identify which lie inside polygon
    for j in range(len(mass)):
        if poly.is_point_in_polygon((glat[j],glon[j])):
            mass[j] = 1
    #-- now convert the mass field to its harmonic representation
    Ylms[i] = gen_stokes(mass.reshape(len(lons),len(lats)),lons,lats,LMIN=LMIN,LMAX=LMAX,UNITS=1,PLM=plm,LOVE=(hl,kl,ll))
    #-- save harmonics to file
    outfile = os.path.join(os.getcwd(),'data','mascon_{0:d}_Ylms_L{1:02d}_{2:.2f}deg.nc'.format(i,LMAX,DDEG))
    ncdf_stokes(np.array(Ylms[i]['clm']),np.array(Ylms[i]['slm']),np.arange(LMAX+1),np.arange(LMAX+1),0,0,FILENAME=outfile,DATE=False)

# TODO
- convert harmonisc back to spatial and plot on top of voronoi regions to make sure they are in the right place
- calculate and plot the sensitivity kernels of the mascons corresponding to the fixed point in `spherical_voronoi.ipynb`